In [1]:
import numpy as np
import pandas as pd
import pydicom
import os
import collections
import sys
import glob
import random
import cv2
import tensorflow as tf
import multiprocessing

from math import ceil, floor
from copy import deepcopy
from tqdm import tqdm
from imgaug import augmenters as iaa

import keras
import keras.backend as K
from keras.callbacks import Callback, ModelCheckpoint
from keras.layers import Dense, Flatten, Dropout
from keras.models import Model, load_model
from keras.utils import Sequence
from keras.losses import binary_crossentropy
from keras.optimizers import Adam

Using TensorFlow backend.


In [2]:
# Install Modules from internet
!pip install efficientnet
!pip install iterative-stratification

In [3]:
# Import Custom Modules
import efficientnet.keras as efn 
from iterstrat.ml_stratifiers import MultilabelStratifiedShuffleSplit

In [7]:
# Seed
SEED = 12345
np.random.seed(SEED)
# tf.set_random_seed(SEED)

# Constants
TEST_SIZE = 0.01
HEIGHT = 256
WIDTH = 256
CHANNELS = 3
TRAIN_BATCH_SIZE = 32
VALID_BATCH_SIZE = 64
SHAPE = (HEIGHT, WIDTH, CHANNELS)

# Folders
DATA_DIR = '/kaggle/input/rsna-intracranial-hemorrhage-detection/rsna-intracranial-hemorrhage-detection/'
TEST_IMAGES_DIR = DATA_DIR + 'stage_2_test/'
TRAIN_IMAGES_DIR = DATA_DIR + 'stage_2_train/'

In [4]:
!ls '/kaggle/input/rsna-intracranial-hemorrhage-detection/rsna-intracranial-hemorrhage-detection'

stage_2_sample_submission.csv  stage_2_test  stage_2_train  stage_2_train.csv


In [5]:
def correct_dcm(dcm):
    x = dcm.pixel_array + 1000
    px_mode = 4096
    x[x>=px_mode] = x[x>=px_mode] - px_mode
    dcm.PixelData = x.tobytes()
    dcm.RescaleIntercept = -1000

def window_image(dcm, window_center, window_width):    
    if (dcm.BitsStored == 12) and (dcm.PixelRepresentation == 0) and (int(dcm.RescaleIntercept) > -100):
        correct_dcm(dcm)
    img = dcm.pixel_array * dcm.RescaleSlope + dcm.RescaleIntercept
    
    # Resize
    img = cv2.resize(img, SHAPE[:2], interpolation = cv2.INTER_LINEAR)
   
    img_min = window_center - window_width // 2
    img_max = window_center + window_width // 2
    img = np.clip(img, img_min, img_max)
    return img

def bsb_window(dcm):
    brain_img = window_image(dcm, 40, 80)
    subdural_img = window_image(dcm, 80, 200)
    soft_img = window_image(dcm, 40, 380)
    
    brain_img = (brain_img - 0) / 80
    subdural_img = (subdural_img - (-20)) / 200
    soft_img = (soft_img - (-150)) / 380
    bsb_img = np.array([brain_img, subdural_img, soft_img]).transpose(1,2,0)
    return bsb_img

def _read(path, SHAPE):
    dcm = pydicom.dcmread(path)
    try:
        img = bsb_window(dcm)
    except:
        img = np.zeros(SHAPE)
    return img

In [9]:
import matplotlib.pyplot as plt

Import the training and test datasets.

In [12]:
base_model =  efn.EfficientNetB0(weights = 'imagenet', include_top = False, \
                                 pooling = 'avg', input_shape = (HEIGHT, WIDTH, 3))

x = base_model.output
x = Dropout(0.125)(x)
output_layer = Dense(6, activation = 'sigmoid')(x)
model = Model(inputs=base_model.input, outputs=output_layer)
model.compile(optimizer = Adam(learning_rate = 0.0001), 
              loss = 'binary_crossentropy',
              metrics = ['acc'])

16809984/16804768 [==============================] - 0s 0us/step


In [13]:
!pip install gdown

  Created wheel for gdown: filename=gdown-3.8.3-cp36-none-any.whl size=8850 sha256=60eafdb73efc62d7de20834e8aece4a416db33f8fa7b5c0536f594bc52163a15
  Stored in directory: /tmp/.cache/pip/wheels/a7/9d/16/9e0bda9a327ff2cddaee8de48a27553fb1efce73133593d066
Successfully built gdown


In [14]:
!gdown https://drive.google.com/uc?id=1FXF1HymYbRf3OlThMTXAa74TRup3AhD_

Downloading...
From: https://drive.google.com/uc?id=1FXF1HymYbRf3OlThMTXAa74TRup3AhD_
To: /kaggle/working/model_effnet_bo_087.h5
16.7MB [00:00, 151MB/s]


In [15]:
model.load_weights('model_effnet_bo_087.h5')

In [22]:
img_data = _read(TRAIN_IMAGES_DIR + '/ID_12cadc6af.dcm', (256, 256))
img_data.shape

(256, 256, 3)

In [35]:
X = np.empty((1, 256,256, 3))
X[0] = img_data
X.shape

(1, 256, 256, 3)

In [36]:
preds = model.predict(X)
preds

array([[0.02540314, 0.00152788, 0.0010443 , 0.0023855 , 0.00326541,
        0.00998502]], dtype=float32)

In [37]:
preds.shape

(1, 6)